In [2]:
import requests 
import pandas as pd
import numpy as np
import os
import requests
from bs4 import BeautifulSoup
import re
from datetime import datetime
import csv
from io import StringIO

In [3]:
df_column_names = [
    "ticker",
    "name",
    "sector",
    "asset_class",
    "market_value",
    "weight",
    "notional_value",
    "shares",
    "price",
    "location",
    "exchange",
    "currency",
    "fx_rate",
    "market_currency",
    "accrual_date",
    # "etfname",
    # "date",
]

In [4]:
ishare_df=pd.read_csv('ishare.csv',encoding='latin-1')
# ishare_df['link']

In [5]:
# headers = {
#     'User-Agent': 'Mozilla/5.0 (Windows NT 10.0; Win64; x64) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/91.0.4472.124 Safari/537.36',
#     'Accept-Language': 'en-US,en;q=0.9',
#     'Accept-Encoding': 'gzip, deflate, br',
#     # [{},{}]

def convert_json_to_df(data):
    final_array=[]
    print("len of data",len(data))
    
    for json_data in data:
        try:
            keys=list(json_data.keys())
            if len(keys)==2 and len(json_data[None])>10 :
                print(json_data)
                ticker=json_data[keys[0]] or None
                name=json_data[keys[1]][0] or None
                sector=json_data[keys[1]][1] or None
                asset_class=json_data[keys[1]][2] or None
                market_value=json_data[keys[1]][3] or None
                weight=json_data[keys[1]][4] or None
                notional_value=json_data[keys[1]][5] or None
                shares=json_data[keys[1]][6] or None
                price=json_data[keys[1]][7] or None
                location=json_data[keys[1]][8] or None
                exchange=json_data[keys[1]][9] or None
                currency=json_data[keys[1]][10] or None
                fx_rate=json_data[keys[1]][11] or None
                market_currency=json_data[keys[1]][12] or None
                accrual_date=json_data[keys[1]][13] or None
                
                final_array.append([ticker,name,sector,asset_class,market_value,weight,notional_value,shares,price,location,exchange,currency,fx_rate,market_currency ,accrual_date])

            else:
                return pd.DataFrame(final_array,columns=df_column_names)
        except Exception as e:
            print("error in convert json",json_data)
            return pd.DataFrame({},columns=df_column_names)
        
    return pd.DataFrame(final_array,columns=df_column_names)




In [6]:
import os

In [19]:



def download_and_save_csv(etfname,csv_url,date):
   
    response = requests.get(csv_url)
    csv_file = StringIO(response.text)
    reader = csv.DictReader(csv_file)

   

    selected_rows =[]
    start_row=10
    # end_row=20
    
    for i, row in enumerate(reader, start=1):
        if start_row <= i:
            selected_rows.append(row)

    if selected_rows:
      
        
        data=convert_json_to_df(selected_rows)
        data['etfname']=etfname
        data['date']=date
     
        return data

     
        
    else:
        print("not available")
        return pd.DataFrame({},columns=df_column_names)
    


In [20]:


def fetch_csv_url_from_web(webpage_url):
    try:
        response = requests.get(webpage_url)
        if response.status_code == 200:
            # Parse the HTML content
            soup = BeautifulSoup(response.content, 'html.parser')

            # Find all anchor tags with .csv links
            csv_links = soup.find_all('a',class_='icon-xls-export')
                                   
            # <a class="icon-xls-export" href="/us/products/239726/ishares-core-sp-500-etf/1467271812596.ajax?fileType=csv&amp;fileName=IVV_holdings&amp;dataType=fund" data-link-event="holdings:holdings">Detailed Holdings and Analytics</a>

            # Extract the href attribute from the first .csv link found
            if csv_links:
                csv_link = csv_links[0]['href']
                return csv_link
            else:
                print("No .csv link found on the webpage.")
                return None
        else:
            print(f"Error fetching webpage: {response.status_code}")
            return None
    except Exception as e:
        print(e,'exception occured')
        return None


Download csv

In [21]:
def is_valid_etfs(etfs):
    valid_etfs=[]
    for etf in etfs:
        # print(etf)
        
        if etf in  list(ishare_df['ticker']):
            print('valid etf found ',etf)
            valid_etfs.append(etf)
    return valid_etfs
    


In [22]:
from datetime import datetime, timedelta

In [23]:
def is_valid_date(startdate,enddate):
    # following validation is

    # 0 DD/MM/YYYY FORMAT
    # 1 start <=end date
    
    # 2 valid dates 
    err=""
    try:
        # Parse dates with flexible formatting for single-digit days/months
        start_date = datetime.strptime(startdate, "%Y/%m/%d")
        end_date = datetime.strptime(enddate, "%Y/%m/%d")
    except ValueError:
         err="Format Error"
         return False,err  # Handle invalid date format

    # Check if start date is less than or equal to end date
    if((start_date <= end_date)==False):
       err='"Start Date must be less than or  equal to end date"'
    return start_date <= end_date,err

    



Fetch By fund name ,date 

In [24]:
def valid_dates_(start_date,end_date):
            
        try:
            # Attempt to convert the string to a datetime object using the specified format
            start_date = datetime.strptime(start_date, "%Y/%m/%d")
            end_date = datetime.strptime(end_date, "%Y/%m/%d")

        except ValueError:
            print(f"Error: Invalid date format. Please check the format of your string date.")


        date_range=[]
        # Loop through dates with a daily step
        for current_date in range((end_date - start_date).days + 1):
            date_to_process = start_date + timedelta(days=current_date)
            # Do something with the date
            date_range.append("".join(str(date_to_process.strftime("%Y/%m/%d")).split("/")))
        return date_range
        


In [25]:
def fetch_data_from_fund(start_date,end_date,fund_name='iShare',etfs=None,all=False):
    # Valid Date checking
    
    BASE_URL='https://www.ishares.com/'
    valid_date,err= is_valid_date(start_date,end_date)
    if(err):
        print(err)
        return
    valid_etfs=is_valid_etfs(etfs)
    if not valid_etfs:
        return " error : ETFs not found in our database"
    # print( "valid Etfs are "+str(valid_etfs))
    main_data_frame=pd.DataFrame({},columns=df_column_names)


    input_dates=valid_dates_(start_date,end_date)

    
    for date in input_dates:
        # For Perticuler Ticker [ETF] we need to check for its data from link available or not

        for etf in valid_etfs:
            curr_etf_link=ishare_df[ishare_df['ticker']==etf]['link'].values[0]
            
            try:
                curr_csv_url=BASE_URL+fetch_csv_url_from_web(curr_etf_link)+'&asOfDate='+date
                print(curr_csv_url)
                data_frame=download_and_save_csv(etf,curr_csv_url,date)
                print("new data frame",data_frame)
                # print("main_data",main_data_frame.head())
                # print("curr_df",data_frame.head())
                if data_frame.shape[0]>0:
                    main_data_frame= pd.concat([main_data_frame,data_frame],ignore_index=True)


                # print("data saved for ETF : {}  and date : {}",format(etf,date))
            except Exception as e:
                print(e)
                return "Data is not available for this period..."
            


            

        # print(str(curr_etf_link))
    if(main_data_frame.shape[0]==0):
        return "No data for this period"
    else:
        main_data_frame.to_csv(f'ETF_{etfs[0]}.csv')
    return "Data Saved For this period"
  
    
    
    
    #create function which takes csv link as input and create a dataframe from it
    
    

In [27]:
etfs=["EFA"]
df=fetch_data_from_fund('2024/05/31','2024/06/12',True,etfs)

valid etf found  EFA
https://www.ishares.com//us/products/239623/ishares-msci-eafe-etf/1467271812596.ajax?fileType=csv&fileName=EFA_holdings&dataType=fund&asOfDate=20240531
len of data 785
{'\ufeffiShares MSCI EAFE ETF': 'NOVO B', None: ['NOVO NORDISK CLASS B', 'Health Care', 'Equity', '1,405,359,070.78', '2.60', '1,405,359,070.78', '10,412,812.00', '134.96', 'Denmark', 'Omx Nordic Exchange Copenhagen A/S', 'USD', '6.87', 'DKK', '-']}
{'\ufeffiShares MSCI EAFE ETF': 'ASML', None: ['ASML HOLDING NV', 'Information Technology', 'Equity', '1,205,309,112.00', '2.23', '1,205,309,112.00', '1,275,000.00', '945.34', 'Netherlands', 'Euronext Amsterdam', 'USD', '0.92', 'EUR', '-']}
{'\ufeffiShares MSCI EAFE ETF': 'NESN', None: ['NESTLE SA', 'Consumer Staples', 'Equity', '902,423,028.81', '1.67', '902,423,028.81', '8,519,474.00', '105.92', 'Switzerland', 'SIX Swiss Exchange', 'USD', '0.90', 'CHF', '-']}
{'\ufeffiShares MSCI EAFE ETF': 'AZN', None: ['ASTRAZENECA PLC', 'Health Care', 'Equity', '767,

In [28]:
etfs=["IWD"]
df=fetch_data_from_fund('2024/05/31','2024/06/12',True,etfs)

valid etf found  IWD
https://www.ishares.com//us/products/239708/ishares-russell-1000-value-etf/1467271812596.ajax?fileType=csv&fileName=IWD_holdings&dataType=fund&asOfDate=20240531
len of data 853
{'\ufeffiShares Russell 1000 Value ETF': 'BRKB', None: ['BERKSHIRE HATHAWAY INC CLASS B', 'Financials', 'Equity', '1,953,261,553.60', '3.52', '1,953,261,553.60', '4,713,469.00', '414.40', 'United States', 'New York Stock Exchange Inc.', 'USD', '1.00', 'USD', '-']}
{'\ufeffiShares Russell 1000 Value ETF': 'JPM', None: ['JPMORGAN CHASE & CO', 'Financials', 'Equity', '1,505,570,889.24', '2.71', '1,505,570,889.24', '7,430,148.00', '202.63', 'United States', 'New York Stock Exchange Inc.', 'USD', '1.00', 'USD', '-']}
{'\ufeffiShares Russell 1000 Value ETF': 'XOM', None: ['EXXON MOBIL CORP', 'Energy', 'Equity', '1,370,346,443.18', '2.47', '1,370,346,443.18', '11,686,393.00', '117.26', 'United States', 'New York Stock Exchange Inc.', 'USD', '1.00', 'USD', '-']}
{'\ufeffiShares Russell 1000 Value ET

In [29]:
etfs=["ITOT"]
df=fetch_data_from_fund('2024/05/31','2024/06/12',True,etfs)

valid etf found  ITOT
https://www.ishares.com//us/products/239724/ishares-core-sp-total-us-stock-market-etf/1467271812596.ajax?fileType=csv&fileName=ITOT_holdings&dataType=fund&asOfDate=20240531
len of data 2525
{'\ufeffiShares Core S&P Total U.S. Stock Market ETF': 'MSFT', None: ['MICROSOFT CORP', 'Information Technology', 'Equity', '3,325,589,409.67', '6.04', '3,325,589,409.67', '8,010,959.00', '415.13', 'United States', 'NASDAQ', 'USD', '1.00', 'USD', '-']}
{'\ufeffiShares Core S&P Total U.S. Stock Market ETF': 'AAPL', None: ['APPLE INC', 'Information Technology', 'Equity', '3,008,096,723.25', '5.46', '3,008,096,723.25', '15,646,797.00', '192.25', 'United States', 'NASDAQ', 'USD', '1.00', 'USD', '-']}
{'\ufeffiShares Core S&P Total U.S. Stock Market ETF': 'NVDA', None: ['NVIDIA CORP', 'Information Technology', 'Equity', '2,919,253,803.83', '5.30', '2,919,253,803.83', '2,662,751.00', '1,096.33', 'United States', 'NASDAQ', 'USD', '1.00', 'USD', '-']}
{'\ufeffiShares Core S&P Total U.S